In [7]:
import numpy as np
import nibabel as nib
import os
import matplotlib.pyplot as plt

# Correcting the fieldmap values from separately acquired GRE magnitude

When acquiring GRE data, with the fine tune option, depending on the FOV selected, the central frequency will change between FOVs. </br>
Therefore its necessary to manually correct the values manually after acquisition. </br>
Important to have the offset values from the scanner, and then we need to select only pixels that are not close to 0. </br>
The correction will be in order of 100 to 300 Hz, and therefore we need to select the pixels that are not lower than a certain treshold.




In [12]:
# Lets load the brain and the cervical FM which both have an intersection.
# On the cervical FM we have some offset values in some regions

brain_fm = nib.load("data/brain_fm/fieldmap_run_1.nii.gz")
cervical_fm = nib.load("data/cervical_fm/fieldmap_run_1.nii.gz")

# So the offset happens in the cervical so we gotta correct this one
# Its imperative to know which one is the fm that needs correcting
fieldmap1 = brain_fm.get_fdata()
fieldmap2 = cervical_fm.get_fdata()


We want to quantify and correct the difference only in the region where they intersect. </br>
For this first: quantify the amount of pixels in Y that are interesecting. Then for X and Z axes it should always be all the pixels.

In [91]:
brain_dim = brain_fm.shape
cervical_dim = cervical_fm.shape
# They should have the same dimensions
corrected_cervical = np.zeros(cervical_dim)
offset_value = 270 # Hz difference on the scanner central frequency - TuneUp value

y_intersect = 34# Amount of pixels in y dimensions. Iteration goes from 0 to 34z

for i in range(cervical_dim[0]-3): # Correcting -3 because brain fov goes from 1 to 141 (itk) and cervical starts at 4 (itk)
    for j in range(y_intersect):
        for k in range(cervical_dim[2]):

            # For the first fieldmap we can use from 1 to 35 (itk_dims)
            value1 = fieldmap1[i,j,k]
            # For the second fieldmap we need to begin from 144 and substract y_intersect value
            # ending in 109 
            value2 = fieldmap2[i+3,143-(34-j),k]

            diff = np.abs(value2 - value1) # Distance in contrast of 2 pixels of overlapping regions

            if value1 < 1 :
                # This is to address the air region that have very low Hz values,
                # Usually should pick between fm1 , depending which one has better results
                corrected_cervical[i+3,143-(34-j),k] = fieldmap1[i,j,k]

            if value2 < 1:
                corrected_cervical[i+3,143-(34-j),k] = fieldmap2[i+3,143-(34-j),k]

            if np.abs(value1) > 1 and np.abs(value2) > 1 and diff > 100 : # np.abs because Hz values are negative also 
                # Now asuming both values are not air, if the difference is bigger than the thrsold
                # Then we need to correct for it
                man_corr = value2 + offset_value
                print("Correcting offset value from ",i+3,143-(34-j),k," value: ",value2, "to: ",man_corr )
                corrected_cervical[i+3,143-(34-j),k] = man_corr # Offset correction

            #if diff < 100 and diff>=1:

            #    corrected_cervical[i,143-j,k] = fieldmap2[i,143-j,k] + np.abs(value2-value1) # If the difference is small we can correct with itself



Correcting offset value from  17 134 11  value:  -97.55338764563203 to:  172.44661235436797
Correcting offset value from  17 134 12  value:  -108.31679812073708 to:  161.68320187926292
Correcting offset value from  17 134 13  value:  -89.21045703813434 to:  180.78954296186566
Correcting offset value from  17 135 8  value:  -88.43796346336603 to:  181.56203653663397
Correcting offset value from  17 135 9  value:  -77.31405598670244 to:  192.68594401329756
Correcting offset value from  17 135 10  value:  -93.12442448362708 to:  176.87557551637292
Correcting offset value from  17 135 11  value:  -106.79756075702608 to:  163.20243924297392
Correcting offset value from  17 135 12  value:  -91.60518711991608 to:  178.39481288008392
Correcting offset value from  17 135 13  value:  -84.00900030136108 to:  185.99099969863892
Correcting offset value from  17 135 14  value:  -84.52399601787329 to:  185.4760039821267
Correcting offset value from  17 135 15  value:  -34.28616387210786 to:  235.7138

In [ ]:

# Now we need to comnplete the rest 
for i in range(cervical_dim[0]):
    for j in range(144 - y_intersect):
        for k in range(cervical_dim[2]):

            corrected_cervical[i,j,k] = fieldmap2[i,j,k]


In [92]:
# Now creating a new nifti and displaying it :)
new_img = nib.Nifti1Image(corrected_cervical, affine = cervical_fm.affine)
nib.save(new_img,"output/correct_dims/iter3.nii.gz")
